# Half-Metallic Graphene Nanoribbon

In this practice, we replicate the results obtained in

*Son, Young-Woo, Marvin L. Cohen, and Steven G. Louie. "Half-metallic graphene nanoribbons." Nature 444.7117 (2006): 347-349*, 

using SIESTA and the sisl library in python.

In [1]:
import numpy as np
import sisl
import sisl.viz
#import plotly.express as px
import os
from Pseudopotential_file_generator import *
import plotly.graph_objects as go

In [2]:
output_path="./GNR/"
siesta_path = "/home/melanie/miniconda3/envs/siesta_env/bin/siesta" 
width=8

# 0. General SIESTA routines

In [3]:
def prepare_SIESTA_inputs(geometry, exp_name, output_path, basis_size='DZP', Nkx=10, Nky=1, Nkz=1, 
                         saveH=True, saveRho=True, relaxation=False, maxForceTotal=0.01, 
                        maxSteps=1000, spin_polarized=False, particular_spins={0:[1, 0, 0], 3:[-1, 0,0]},
                         electric_field=None, save_total_potential=False, use_DM=False, take_DM_from=None,
                         ):
    out_dir = output_path+f"{exp_name}_Basis_{basis_size}_Nkx={Nkx}_Nky={Nky}_Nkz={Nkz}/"
    os.makedirs(out_dir, exist_ok=True)

    # generate pseudopotential files
    generate_C_psf(out_dir+"/C.psf")
    generate_H_psf(out_dir+"/H.psf")
    # generate the initial ansatz geometry file
    geometry.write(out_dir+ "/geom.fdf")

    # Inside this directory, open a RUN.fdf file, as our main input file. 
    with open(out_dir+ '/RUN.fdf', 'w') as f:
        # We include the fdf file that contains the geometry, with the %include statement
        f.write("%include geom.fdf \n")
        # the basis size and basis parameter input.
        f.write(f"PAO.BasisSize {basis_size}\n")
        f.write("DM.MixingWeight  0.100\nDM.NumberPulay  3\n")
        if saveH:
            # We want the converged Hamiltonian to be saved
            f.write("TS.HS.Save true\n")
        if saveRho:
            # Save the electronic density
            f.write("SaveRho true\n")
        # Define the employed k-space grid
        k_grid=f"%block kgrid.MonkhorstPack\n{Nkx} 0 0  0\n 0 {Nky} 0  0\n   0 0 {Nkz}  0\n%endblock kgrid.MonkhorstPack\n"
        f.write(k_grid)
        if relaxation:
            # Conjugate gradient minimization for geometry relaxation 
            #   SIESTA will compute the convergent electronic states with the siesta algorithm
            #   at each iteration of the geometry relaxation
            f.write("MD.TypeOfRun CG\n")
            # stopping criterion, if max force on atoms is this, stop
            f.write(f"MD.MaxForceTol {maxForceTotal} eV/Ang\n")
            # maximum steps, if convergence not achieved at this number of steps
            #   stop the search
            f.write(f"MD.Steps {maxSteps}\n") # maximum steps
        if spin_polarized:
            # set spin polarized calculation
            f.write("Spin polarized\n") 
            if particular_spins is not None:
                f.write("%block DM.InitSpin\n")
                for k,v in particular_spins.items():
                    f.write(f"{k} {v[0]} {v[1]} {v[2]}\n")
                f.write(f"%endblock DM.InitSpin\n")
        if electric_field is not None:
            f.write(f"%block ExternalElectricField\n{electric_field[0]} {electric_field[1]} {electric_field[2]} V/Ang\n%endblock ExternalElectricField\n")
        if save_total_potential:
            f.write("SaveTotalPotential true\n")
        if use_DM:
            os.system(f"cp {take_DM_from}/siesta.DM {out_dir}/siesta.DM")
            # if already a good enough initial density matrix ansatz is available
            f.write("DM.UseSaveDM true\n") 
    return out_dir

def run_siesta_on(path_to_run, siesta_path):
    os.system(f"cd {path_to_run}; {siesta_path} RUN.fdf > RUN.out")

## 1. Generation of the Nanoribbon Structure 

In [4]:
gnr=sisl.geom.graphene_nanoribbon(width=width, bond=1.42, atoms=None, kind='zigzag')
# Plot it to see that it is what we wanted
gnr.plot(axes="xy")

FigureWidget({
    'data': [{'line': {'color': '#cccccc', 'width': 3},
              'mode': 'lines',
        …

In [5]:
edgeC_idxs=[0,7]

We add the hydrogen atoms.

In [6]:
CH=CH = 1.09 #A Benzene distance from C to H
h_atoms = sisl.Geometry(np.array([gnr.axyz()[edgeC_idxs[0]]-np.array([0,CH,0]),
                                  gnr.axyz()[edgeC_idxs[1]]+np.array([0,CH,0]) ]), 
         [sisl.Atom('H'), sisl.Atom('H')])
gnr=gnr.insert(-1, h_atoms)
gnr.plot(axes="xy")

FigureWidget({
    'data': [{'line': {'color': '#cccccc', 'width': 3},
              'mode': 'lines',
        …

In [8]:
relaxation_dir = prepare_SIESTA_inputs(geometry=gnr, exp_name=f"GNR_width_{width}_Relaxation_", 
                        output_path=output_path, basis_size='DZP', Nkx=10, Nky=1, Nkz=1, 
                        saveH=True, saveRho=True, relaxation=True, maxForceTotal=0.01, 
                        maxSteps=1000, spin_polarized=False, particular_spins=None,
                        electric_field=None, save_total_potential=False, use_DM=False, take_DM_from=None)

In [8]:
run_siesta_on(relaxation_dir, siesta_path)

Job completed


In [9]:
# Read the resulting Hamiltonian
H = sisl.get_sile(f"{relaxation_dir}/RUN.fdf").read_hamiltonian()

# Extract the relaxed structure
gnr=H.geometry

#plot it
gnr.plot(axes='xy')

FigureWidget({
    'data': [{'line': {'color': '#cccccc', 'width': 3},
              'mode': 'lines',
        …

We can see the progress of the simulation with `tail RUN.out -f`. Then, `grep constrained RUN.out` will show us the maximum forces of each iteration. Finally, using `vmd siesta.ANI -xyz`, the animation for the relaxation can be seen.

### Band Structure of the No-spin polarization case

In [10]:
# We need to define a path of k points
band_struct = sisl.BandStructure(H, points=[[0, 0, 0], [0.5, 0, 0], ],
    divisions=100, names=[r"0", "pi"],
)

In [11]:
# H.plot.wavefunction(i=15, axes="xy",z_range=(0,5)) #this allows us to see a molecular wavefunction -the 15th one

In [11]:
# Then we can plot the bands
band_struct.plot(Erange=[-3, 3])

FigureWidget({
    'data': [{'hoverinfo': 'name',
              'hovertemplate': '%{y:.2f} eV',
              …

In [12]:
# Get the fatbands plot
fatbands = band_struct.plot.fatbands(Erange=[-3, 3])
# Split the contributions by the n and l quantum numbers
fatbands.split_groups(on="atoms", scale=10)

FigureWidget({
    'data': [{'fill': 'toself',
              'legendgroup': ' | atoms=0',
              'line'…

Son todos 2pz especialmente, excepto el intransigente, que resulta ser 2py o 2pz. si ploteamos en función de los átomos vemos que los problemáticos sean los de la frontera del ribbon, el átomo 0 y el 3.

Bandas planas es inverso de la curvatura es la masa efectiva tendiente a infinito. Entonces eso vol dir que son estados muy localizados en algún lugar de la estructura! Es que la conductividad/mobilidad de esos electrones será súper ínfimo.

In [13]:
# Get the PDOS plot
pdos_plot = H.plot.pdos(
    kgrid=[50,1,1], nE=1000, Erange=[-3, 3],
    distribution={"method": "gaussian", "smearing": 0.1}
)
# Split the contributions by the n and l quantum numbers
pdos_plot.split_DOS(on="atom")

FigureWidget({
    'data': [{'line': {'dash': 'solid', 'width': 1.0},
              'mode': 'lines',
         …

In [38]:
rho = sisl.get_sile(f"{relaxation_dir}/RUN.fdf").read_grid("RHO")
rho.plot(axes="xy", plot_geom=True)

FigureWidget({
    'data': [{'type': 'heatmap',
              'uid': 'fcc128c5-477f-4046-9c19-84f9fde24a85',
 …

# 2. Spin Polarization, no Electric Field

Import the relaxed geometry.

In [10]:
H = sisl.get_sile(f"{relaxation_dir}/RUN.fdf").read_hamiltonian()
gnr=H.geometry
no_E_field={'all_aligned':{}, 'edge_spins_aligned':{}, 'edge_spins_antialigned':{}}

Prepare SIESTA input files

In [11]:
no_E_field['all_aligned']['dir'] = prepare_SIESTA_inputs(geometry=gnr, exp_name=f"GNR_width_{width}_spin_all_aligned_", 
                        output_path=output_path,basis_size='DZP', Nkx=10, Nky=1, Nkz=1, 
                         saveH=True, saveRho=True, relaxation=False, maxForceTotal=0.01, 
                        maxSteps=1000, spin_polarized=True, particular_spins=None,
                         electric_field=None, save_total_potential=False, use_DM=False, take_DM_from=None)

In [12]:
no_E_field['edge_spins_aligned']['dir'] = prepare_SIESTA_inputs(geometry=gnr, exp_name=f"GNR_width_{width}_edge_spins_aligned_",
                        output_path=output_path, basis_size='DZP', Nkx=10, Nky=1, Nkz=1, 
                         saveH=True, saveRho=True, relaxation=False, maxForceTotal=0.01, 
                        maxSteps=1000, spin_polarized=True, 
                        particular_spins={(edgeC_idxs[0]+1):[1.0, 0.0, 0.0], (edgeC_idxs[1]+1):[1.0, 0.0,0.0]},
                         electric_field=None, save_total_potential=False, use_DM=False, take_DM_from=None)

In [13]:
no_E_field['edge_spins_antialigned']['dir'] = prepare_SIESTA_inputs(geometry=gnr,exp_name=f"GNR_width_{width}_edge_spins_antialigned_", 
                        output_path=output_path,basis_size='DZP', Nkx=10, Nky=1, Nkz=1, 
                         saveH=True, saveRho=True, relaxation=False, maxForceTotal=0.01, 
                        maxSteps=1000, spin_polarized=True, 
                        particular_spins={(edgeC_idxs[0]+1):[1.0, 0.0, 0.0], (edgeC_idxs[1]+1):[-1.0, 0.0,0.0]},
                         electric_field=None, save_total_potential=False, use_DM=False, take_DM_from=None)

Run SIESTA

In [33]:
for mode in no_E_field.keys():
    run_siesta_on(no_E_field[mode]['dir'], siesta_path)

Job completed
Job completed


Obtain resulting diagram data

In [45]:
for mode in no_E_field.keys():
    # Read the resulting Hamiltonians
    no_E_field[mode]['H'] = sisl.get_sile(f"{no_E_field[mode]['dir']}/RUN.fdf").read_hamiltonian()
    
    # Compute band structure plots
    no_E_field[mode]['band_struct'] = sisl.BandStructure(no_E_field[mode]['H'],
        points=[[0, 0, 0], [0.5, 0, 0], ],
        divisions=100, names=[r"0", "pi"],)

    # Get the PDOS plots
    no_E_field[mode]['pdos_plot'] = no_E_field[mode]['H'].plot.pdos(
        kgrid=[50,1,1], nE=1000, Erange=[-3, 3],
        distribution={"method": "gaussian", "smearing": 0.03}
    )

In [41]:
no_E_field['all_aligned']['band_struct'].plot(Erange=[-3, 3])

FigureWidget({
    'data': [{'hoverinfo': 'name',
              'hovertemplate': '%{y:.2f} eV',
              …

In [43]:
# Get the fatbands plot
fatbands = no_E_field['all_aligned']['band_struct'].plot.fatbands(Erange=[-3, 3])
# Split the contributions by the n and l quantum numbers
fatbands.split_groups(on="atoms", scale=10)

FigureWidget({
    'data': [{'fill': 'toself',
              'legendgroup': ' | atoms=0',
              'line'…

In [46]:
# Split the contributions by the n and l quantum numbers
no_E_field['all_aligned']['pdos_plot'].split_DOS(on="atom")

FigureWidget({
    'data': [{'line': {'dash': 'solid', 'width': 1.0},
              'mode': 'lines',
         …

In [47]:
no_E_field['edge_spins_aligned']['band_struct'].plot(Erange=[-3, 3])

FigureWidget({
    'data': [{'hoverinfo': 'name',
              'hovertemplate': '%{y:.2f} eV',
              …

In [48]:
fatbands = no_E_field['edge_spins_aligned']['band_struct'].plot.fatbands(Erange=[-3, 3])
fatbands.split_groups(on="atoms", scale=10)

FigureWidget({
    'data': [{'fill': 'toself',
              'legendgroup': ' | atoms=0',
              'line'…

In [49]:
no_E_field['edge_spins_aligned']['pdos_plot'].split_DOS(on="atom")

FigureWidget({
    'data': [{'line': {'dash': 'solid', 'width': 1.0},
              'mode': 'lines',
         …

In [50]:
no_E_field['edge_spins_antialigned']['band_struct'].plot(Erange=[-3, 3])

FigureWidget({
    'data': [{'hoverinfo': 'name',
              'hovertemplate': '%{y:.2f} eV',
              …

In [70]:
fatbands = no_E_field['edge_spins_antialigned']['band_struct'].plot.fatbands(Erange=[-3, 3])

In [156]:
fatbands.split_groups(on='atoms+spin',scale=5)
fatbands.update_settings(groups=[{"atom":0, "spin":1, "name":"Atom R spin up"},
                                    {"atom":7, "spin":0, "name":"Atom L spin down"},
                         {"atom":7, "spin":1, "name":"Atom L spin up"},
                          {"atom":0, "spin":0, "name":"Atom R spin down"}])

FigureWidget({
    'data': [{'fill': 'toself',
              'legendgroup': 'Atom R spin up',
              'l…

In [26]:
a=with_E_field[0]['pdos_plot'].split_DOS(on="atom+spin")
a.update_settings(groups=[{"atom":0, "spin":1, "name":"Atom R spin up"},
                                    {"atom":7, "spin":0, "name":"Atom L spin down"},
                         {"atom":7, "spin":1, "name":"Atom L spin up"},
                          {"atom":0, "spin":0, "name":"Atom R spin down"}])

FigureWidget({
    'data': [{'line': {'dash': 'solid', 'width': 1.0},
              'mode': 'lines',
         …

In [87]:
no_E_field['edge_spins_antialigned']['pdos_plot'].split_DOS(on="atom+spin")

FigureWidget({
    'data': [{'line': {'dash': 'solid', 'width': 1.0},
              'mode': 'lines',
         …

In [106]:
no_E_field['edge_spins_antialigned']['H']

<sisl.physics.Hamiltonian na=18, no=218, nsc=[5 1 1], dim=3, nnz=91366, spin=polarized>

Plot the Wavefunctions

In [126]:
no_E_field['all_aligned']['H'].plot.wavefunction(i=33,spin=0, k=[0.5, 0, 0], axes="xy",z_range=(0,5)) 
#this allows us to see a molecular wavefunction

info:0: SislInfo:

wavefunction: k != Gamma is currently untested!



FigureWidget({
    'data': [{'name': 'WF 33 (-0.35 eV)',
              'type': 'heatmap',
              'uid':…

Obtain the converged energy of each case

In [92]:
for mode in no_E_field.keys():
    with open(no_E_field[mode]['dir']+'/RUN.out', 'r') as f:
        for line in f.readlines():
            if 'Total =' in line:
                no_E_field[mode]['E'] = float(line.split('Total =')[-1])
    print(f"Mode : {mode} Energy : {no_E_field[mode]['E']:.10} eV")

Mode : all_aligned Energy : -2617.12879 eV
Mode : edge_spins_aligned Energy : -2617.128796 eV
Mode : edge_spins_antialigned Energy : -2617.129309 eV


# 3. Spin Polarization, varying Electric Field

In [14]:
H = sisl.get_sile(f"{relaxation_dir}/RUN.fdf").read_hamiltonian()
gnr=H.geometry
with_E_field={0:{'dir':no_E_field['edge_spins_antialigned']['dir']}, 0.05:{}, 0.1:{}, 0.2:{}, 0.5:{}} # keys in V/A

Prepare SIESTA input

In [15]:
for mode in with_E_field.keys():
    if mode!=0:
        with_E_field[mode]['dir']= prepare_SIESTA_inputs(geometry=gnr, exp_name=f"GNR_width_{width}_edge_spins_antialigned_E_{mode}_", 
             output_path=output_path,basis_size='DZP', Nkx=10, Nky=1, Nkz=1, 
            saveH=True, saveRho=True, relaxation=False, maxForceTotal=0.01, 
            maxSteps=1000, spin_polarized=True, 
            particular_spins={(edgeC_idxs[0]+1):[1, 0, 0], (edgeC_idxs[1]+1):[-1, 0,0]},
            electric_field=np.array([0, mode, 0]), save_total_potential=True, use_DM=True,
            take_DM_from=no_E_field['edge_spins_antialigned']['dir']) 

Run SIESTA

In [22]:
for mode in with_E_field.keys():
    if mode!=0:
        run_siesta_on(with_E_field[mode]['dir'], siesta_path)

Job completed


Obtain resulting diagram data

In [23]:
for mode in with_E_field.keys():
    # Read the resulting Hamiltonians
    with_E_field[mode]['H'] = sisl.get_sile(f"{with_E_field[mode]['dir']}/RUN.fdf").read_hamiltonian()
    
    # Compute band structure plots
    with_E_field[mode]['band_struct'] = sisl.BandStructure(with_E_field[mode]['H'],
        points=[[0, 0, 0], [0.5, 0, 0], ],
        divisions=100, names=[r"0", "pi"],)

    # Get the PDOS plots
    with_E_field[mode]['pdos_plot'] = with_E_field[mode]['H'].plot.pdos(
        kgrid=[50,1,1], nE=1000, Erange=[-3, 3],
        distribution={"method": "gaussian", "smearing": 0.03}
    )

In [16]:
with_E_field[0]['band_struct'].plot(Erange=[-3, 3])

FigureWidget({
    'data': [{'hoverinfo': 'name',
              'hovertemplate': '%{y:.2f} eV',
              …

In [17]:
with_E_field[0.05]['band_struct'].plot(Erange=[-3, 3])

FigureWidget({
    'data': [{'hoverinfo': 'name',
              'hovertemplate': '%{y:.2f} eV',
              …

In [18]:
with_E_field[0.1]['band_struct'].plot(Erange=[-3, 3])

FigureWidget({
    'data': [{'hoverinfo': 'name',
              'hovertemplate': '%{y:.2f} eV',
              …

In [19]:
with_E_field[0.2]['band_struct'].plot(Erange=[-3, 3])

FigureWidget({
    'data': [{'hoverinfo': 'name',
              'hovertemplate': '%{y:.2f} eV',
              …

In [24]:
with_E_field[0.5]['band_struct'].plot(Erange=[-3, 3])

FigureWidget({
    'data': [{'hoverinfo': 'name',
              'hovertemplate': '%{y:.2f} eV',
              …

In [159]:
fatbands=with_E_field[0]['band_struct'].plot.fatbands(Erange=[-3, 3])
fatbands.split_groups(on='atoms+spin',scale=5)
fatbands.update_settings(groups=[{"atom":0, "spin":1, "name":"Atom R spin up"},
                                    {"atom":7, "spin":0, "name":"Atom L spin down"},
                         {"atom":7, "spin":1, "name":"Atom L spin up"},
                          {"atom":0, "spin":0, "name":"Atom R spin down"}])

FigureWidget({
    'data': [{'fill': 'toself',
              'legendgroup': 'Atom R spin up',
              'l…

In [171]:
fatbands=with_E_field[0.05]['band_struct'].plot.fatbands(Erange=[-3, 3])
fatbands.split_groups(on='atoms+spin',scale=5)
fatbands.update_settings(groups=[{"atom":0, "spin":1, "name":"Atom R spin up"},
                                    {"atom":7, "spin":0, "name":"Atom L spin down"},
                         {"atom":7, "spin":1, "name":"Atom L spin up"},
                          {"atom":0, "spin":0, "name":"Atom R spin down"}])

FigureWidget({
    'data': [{'fill': 'toself',
              'legendgroup': 'Atom R spin up',
              'l…

In [15]:
fatbands=with_E_field[0.1]['band_struct'].plot.fatbands(Erange=[-3, 3])
fatbands.split_groups(on='atoms+spin',scale=5)
fatbands.update_settings(groups=[{"atom":0, "spin":1, "name":"Atom R spin up"},
                                    {"atom":7, "spin":0, "name":"Atom L spin down"},
                         {"atom":7, "spin":1, "name":"Atom L spin up"},
                          {"atom":0, "spin":0, "name":"Atom R spin down"}])

FigureWidget({
    'data': [{'fill': 'toself',
              'legendgroup': 'Atom R spin up',
              'l…

In [170]:
fatbands=with_E_field[0.2]['band_struct'].plot.fatbands(Erange=[-3, 3])
fatbands.split_groups(on='atoms+spin',scale=5)
fatbands.update_settings(groups=[{"atom":0, "spin":1,"color":"blue", "name":"Atom R spin up"},
                                    {"atom":7, "spin":0, "name":"Atom L spin down"},
                         {"atom":7, "spin":1, "name":"Atom L spin up"},
                          {"atom":0, "spin":0, "name":"Atom R spin down"}])

FigureWidget({
    'data': [{'fill': 'toself',
              'legendgroup': 'Atom R spin up',
              'l…

In [151]:
pdos_plot=with_E_field[0]['pdos_plot']
pdos_plot.update_settings(requests=[
    {"atoms": 0, 'scale':-1, "spin":0, "color":"red", "name":"Atom R Spin down"},
    {"atoms": 0, 'scale':-1, "spin":1,  "color":"blue", "name":"Atom R Spin up"},
    {"atoms": 7, 'scale':1, "spin":0, "color":"red", "name":"Atom L Spin down"},
    {"atoms": 7, 'scale':1, "spin":1,  "color":"blue", "name":"Atom L Spin up"}], fill='tonexty'
                         ).update_traces(fill="tozerox").add_trace(go.Scatter(
    x=[0.5, -0.5],
    y=[0.8, 0.8 ],
    mode="text",
    name="which atom's DOS?",
    text=["Edge Atom R", "Edge Atom L"],
    textposition="bottom center"
)).add_trace(go.Scatter(
    x=[0.5, -0.5, 0.5, -0.5],
    y=[0.3, 0.3, -0.5, -0.5 ],
    mode="text",
    name="which spin's DOS?",
    text=["down", "up", "up", "down"],
    textposition="bottom center"
))

In [152]:
pdos_plot=with_E_field[0.05]['pdos_plot']
pdos_plot.update_settings(requests=[
    {"atoms": 0, 'scale':-1, "spin":0, "color":"red", "name":"Atom R Spin down"},
    {"atoms": 0, 'scale':-1, "spin":1,  "color":"blue", "name":"Atom R Spin up"},
    {"atoms": 7, 'scale':1, "spin":0, "color":"red", "name":"Atom L Spin down"},
    {"atoms": 7, 'scale':1, "spin":1,  "color":"blue", "name":"Atom L Spin up"}], fill='tonexty'
                         ).update_traces(fill="tozerox").add_trace(go.Scatter(
    x=[0.5, -0.5],
    y=[0.8, 0.8 ],
    mode="text",
    name="which atom's DOS?",
    text=["Edge Atom R", "Edge Atom L"],
    textposition="bottom center"
)).add_trace(go.Scatter(
    x=[0.5, -0.5, 0.5, -0.5],
    y=[0.3, 0.3, -0.5, -0.5 ],
    mode="text",
    name="which spin's DOS?",
    text=["down", "up", "up", "down"],
    textposition="bottom center"
))

In [153]:
pdos_plot=with_E_field[0.1]['pdos_plot']
pdos_plot.update_settings(requests=[
    {"atoms": 0, 'scale':-1, "spin":0, "color":"red", "name":"Atom R Spin down"},
    {"atoms": 0, 'scale':-1, "spin":1,  "color":"blue", "name":"Atom R Spin up"},
    {"atoms": 7, 'scale':1, "spin":0, "color":"red", "name":"Atom L Spin down"},
    {"atoms": 7, 'scale':1, "spin":1,  "color":"blue", "name":"Atom L Spin up"}], fill='tonexty'
                         ).update_traces(fill="tozerox").add_trace(go.Scatter(
    x=[0.5, -0.5],
    y=[0.8, 0.8 ],
    mode="text",
    name="which atom's DOS?",
    text=["Edge Atom R", "Edge Atom L"],
    textposition="bottom center"
)).add_trace(go.Scatter(
    x=[0.5, -0.5, 0.5, -0.5],
    y=[0.3, 0.3, -0.5, -0.5 ],
    mode="text",
    name="which spin's DOS?",
    text=["down", "up", "up", "down"],
    textposition="bottom center"
))

In [154]:
pdos_plot=with_E_field[0.2]['pdos_plot']
pdos_plot.update_settings(requests=[
    {"atoms": 0, 'scale':-1, "spin":0, "color":"red", "name":"Atom R Spin down"},
    {"atoms": 0, 'scale':-1, "spin":1,  "color":"blue", "name":"Atom R Spin up"},
    {"atoms": 7, 'scale':1, "spin":0, "color":"red", "name":"Atom L Spin down"},
    {"atoms": 7, 'scale':1, "spin":1,  "color":"blue", "name":"Atom L Spin up"}], fill='tonexty'
                         ).update_traces(fill="tozerox").add_trace(go.Scatter(
    x=[0.5, -0.5],
    y=[0.8, 0.8 ],
    mode="text",
    name="which atom's DOS?",
    text=["Edge Atom R", "Edge Atom L"],
    textposition="bottom center"
)).add_trace(go.Scatter(
    x=[0.5, -0.5, 0.5, -0.5],
    y=[0.3, 0.3, -0.5, -0.5 ],
    mode="text",
    name="which spin's DOS?",
    text=["down", "up", "up", "down"],
    textposition="bottom center"
))

In [25]:
pdos_plot=with_E_field[0.5]['pdos_plot']
pdos_plot.update_settings(requests=[
    {"atoms": 0, 'scale':-1, "spin":0, "color":"red", "name":"Atom R Spin down"},
    {"atoms": 0, 'scale':-1, "spin":1,  "color":"blue", "name":"Atom R Spin up"},
    {"atoms": 7, 'scale':1, "spin":0, "color":"red", "name":"Atom L Spin down"},
    {"atoms": 7, 'scale':1, "spin":1,  "color":"blue", "name":"Atom L Spin up"}], fill='tonexty'
                         ).update_traces(fill="tozerox").add_trace(go.Scatter(
    x=[0.5, -0.5],
    y=[0.8, 0.8 ],
    mode="text",
    name="which atom's DOS?",
    text=["Edge Atom R", "Edge Atom L"],
    textposition="bottom center"
)).add_trace(go.Scatter(
    x=[0.5, -0.5, 0.5, -0.5],
    y=[0.3, 0.3, -0.5, -0.5 ],
    mode="text",
    name="which spin's DOS?",
    text=["down", "up", "up", "down"],
    textposition="bottom center"
))

In [18]:
rho = sisl.get_sile(f"{with_E_field[0.5]['dir']}/RUN.fdf").read_grid("VT")
rho.plot(axes="y", plot_geom=True)

FigureWidget({
    'data': [{'mode': 'lines',
              'opacity': 1,
              'type': 'scatter',
   …

E de la antiferromagnetica es 0.02 eV más baja que la ferromagnética. Y eso en fk de la T será o no sufcte para que se estabilice. Y con esto sacas la cte de acoplamiento y ahora puedes hacer modelos más macroscópicos.
Y aT amb la Ek media es 0.026 eV asike no es mucho más estable digamos, peero sí.

Si haces más ancho el ribbon se haría una cte de acoplamiento, que es la diffcia de energías se haría más pequeña. Si haces más istue ba energía de acoplamiento altuaue.